In [1]:
# Importing Libraries
import numpy as np
import scipy as sp
import seaborn as sns
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, GridSearchCV, KFold
from sklearn.tree import DecisionTreeRegressor, DecisionTreeClassifier
from sklearn.ensemble import AdaBoostRegressor, AdaBoostClassifier, \
    GradientBoostingClassifier, GradientBoostingRegressor, \
    RandomForestClassifier, RandomForestRegressor
from sklearn.metrics import r2_score
from pymatgen.core import Element, Composition, periodic_table
from functools import partial


In [2]:
# Loading training and testing data
train= pd.read_csv("train.csv",index_col=False)
test= pd.read_csv("test.csv",index_col=False)

# Querying materials and their properties based on training data
from pymatgen.ext.matproj import MPRester
mpr = MPRester("241iWwhTEOaNmC6V")

# Using material IDs provided in training data to get corresponding information from MPD
data = mpr.query(criteria={"task_id": {"$in":train["material_id"].to_list()}}, properties=["material_id","energy",
        "energy_per_atom",
        "volume",
        "formation_energy_per_atom",
        "nsites",
        "pretty_formula",                                                                                  
        "nelements",
        "density",  "band_gap"])
df = pd.DataFrame(data)

  0%|          | 0/5619 [00:00<?, ?it/s]

In [3]:
#Making list of possible noble gases 
nobles = ["He","Ne", "Ar", "Kr", "Xe", "Rn", "Og"]
filt_data = df

#Iterating through data and using pandas drop function to filter out materials containing noble gas elements 
for i in nobles:
    filt_data = filt_data.drop(filt_data[filt_data['pretty_formula'].str.contains(i)].index)
 

In [4]:
listA = [a for a in filt_data["pretty_formula"]]
listB = [Composition(a) for a in listA]
listC = [a.elements for a in listB]

editC = [item for sublist in listC for item in sublist]
unique_editC = set(editC)
unique_editC

UL_editC = [a for a in unique_editC]
cprops = [a.data for a in UL_editC]

peel=set(UL_editC)
sy_editC = [a.symbol for a in UL_editC]
sy_editC

cprops_df = pd.DataFrame(cprops, index=sy_editC)

cprops_df.head()

Atomic mass  Atomic no                                    Atomic orbitals  \
H      1.007940          1                                  {'1s': -0.233471}   
Li     6.941000          3                  {'1s': -1.878564, '2s': -0.10554}   
Be     9.012182          4                 {'1s': -3.856411, '2s': -0.205744}   
B     10.811000          5  {'1s': -6.564347, '2p': -0.136603, '2s': -0.34...   
C     12.010700          6  {'1s': -9.947718, '2p': -0.199186, '2s': -0.50...   

    Atomic radius Atomic radius calculated Boiling point  \
H            0.25                     0.53       20.28 K   
Li           1.45                     1.67        1615 K   
Be           1.05                     1.12        2742 K   
B            0.85                     0.87        4200 K   
C            0.70                     0.67        4300 K   

             Brinell hardness Bulk modulus  \
H   no data MN m<sup>-2</sup>  no data GPa   
Li  no data MN m<sup>-2</sup>       11 GPa   
Be      600 MN m<sup>-2</sup>      130 GPa   
B   no data MN m<sup>-2</sup>      320 GPa   
C   no data MN m<sup>-2</sup>       33 GPa   

   Coefficient of linear thermal expansion Common oxidation states  ...  \
H   no data x10<sup>-6</sup>K<sup>-1</sup>                 [-1, 1]  ...   
Li       46 x10<sup>-6</sup>K<sup>-1</sup>                     [1]  ...   
Be     11.3 x10<sup>-6</sup>K<sup>-1</sup>                     [2]  ...   
B         6 x10<sup>-6</sup>K<sup>-1</sup>                     [3]  ...   
C       7.1 x10<sup>-6</sup>K<sup>-1</sup>                 [-4, 4]  ...   

              NMR Quadrupole Moment Metallic radius iupac_ordering  \
H                     {'H-2': 2.86}         no data             92   
Li  {'Li-6': -0.808, 'Li-7': -40.1}            1.52             11   
Be                  {'Be-9': 52.88}            1.12             17   
B    {'B-10': 84.59, 'B-11': 40.59}         no data             81   
C                   {'C-11': 33.27}         no data             86   

   IUPAC ordering Ground level  \
H              92        2S1/2   
Li             11        2S1/2   
Be             17          1S0   
B              81       2P°1/2   
C              86          3P0   

                                  Ionization energies Electron affinity  \
H                                   [13.598434599702]          0.754598   
Li             [5.391714996, 75.640097, 122.45435914]          0.618049   
Be      [9.322699, 18.21115, 153.896205, 217.7185861]         -0.520000   
B   [8.298019, 25.15483, 37.93059, 259.3715, 340.2...          0.279723   
C   [11.260288, 24.383154, 47.88778, 64.49352, 392...          1.262114   

    Ionic radii Ionic radii hs Ionic radii ls  
H           NaN            NaN            NaN  
Li   {'1': 0.9}            NaN            NaN  
Be  {'2': 0.59}            NaN            NaN  
B   {'3': 0.41}            NaN            NaN  
C    {'4': 0.3}            NaN            NaN  

[5 rows x 44 columns]

In [5]:
droplist = ['Ionic radii',
    'Ionic radii hs', 
     'Ionic radii ls',
     'iupac_ordering', 
     'IUPAC ordering', 
     'NMR Quadrupole Moment', 
     'Reflectivity',
     'Refractive index', 
     'Rigidity modulus', 
     'Shannon radii',
     'Superconduction temperature',
     'Mendeleev no',       
     'Mineral hardness',
     'Molar volume',
     'Name',
     'Oxidation states',
     'ICSD oxidation states',
     'Brinell hardness',
     'Atomic orbitals', 
     'Coefficient of linear thermal expansion',
     'Atomic orbitals',
     'Electronic structure',
     'Electrical resistivity',
     'Ground level'
           ]


cprops_df = cprops_df.drop(columns=droplist)
cprops_df

Atomic mass  Atomic no  Atomic radius Atomic radius calculated  \
H      1.007940          1           0.25                     0.53   
Li     6.941000          3           1.45                     1.67   
Be     9.012182          4           1.05                     1.12   
B     10.811000          5           0.85                     0.87   
C     12.010700          6           0.70                     0.67   
..          ...        ...            ...                      ...   
Pb   207.200000         82           1.80                     1.54   
Bi   208.980400         83           1.60                     1.43   
Ac   227.000000         89           1.95                  no data   
Th   232.038060         90           1.80                  no data   
U    238.028910         92           1.75                  no data   

   Boiling point Bulk modulus Common oxidation states Critical temperature  \
H        20.28 K  no data GPa                 [-1, 1]                 33 K   
Li        1615 K       11 GPa                     [1]               3223 K   
Be        2742 K      130 GPa                     [2]            no data K   
B         4200 K      320 GPa                     [3]            no data K   
C         4300 K       33 GPa                 [-4, 4]            no data K   
..           ...          ...                     ...                  ...   
Pb        2022 K       46 GPa                  [2, 4]            no data K   
Bi        1837 K       31 GPa                     [3]            no data K   
Ac        3573 K  no data GPa                     [3]            no data K   
Th        5093 K       54 GPa                     [4]            no data K   
U         4200 K      100 GPa                     [6]            no data K   

             Density of solid Liquid range  ... Poissons ratio  \
H   no data kg m<sup>-3</sup>       6.27 K  ...        no data   
Li      535 kg m<sup>-3</sup>    1161.31 K  ...        no data   
Be     1848 kg m<sup>-3</sup>       1182 K  ...          0.032   
B      2460 kg m<sup>-3</sup>       1851 K  ...        no data   
C      2267 kg m<sup>-3</sup>        500 K  ...        no data   
..                        ...          ...  ...            ...   
Pb    11340 kg m<sup>-3</sup>    1421.39 K  ...           0.44   
Bi     9780 kg m<sup>-3</sup>     1292.6 K  ...           0.33   
Ac    10070 kg m<sup>-3</sup>       2250 K  ...        no data   
Th    11724 kg m<sup>-3</sup>       2978 K  ...           0.27   
U     19050 kg m<sup>-3</sup>     2794.7 K  ...           0.23   

                      Thermal conductivity Van der waals radius  \
H   0.1805 W m<sup>-1</sup> K<sup>-1</sup>                 1.10   
Li      85 W m<sup>-1</sup> K<sup>-1</sup>                 1.82   
Be     190 W m<sup>-1</sup> K<sup>-1</sup>                 1.53   
B       27 W m<sup>-1</sup> K<sup>-1</sup>                 1.92   
C      140 W m<sup>-1</sup> K<sup>-1</sup>                 1.70   
..                                     ...                  ...   
Pb      35 W m<sup>-1</sup> K<sup>-1</sup>                 2.02   
Bi       8 W m<sup>-1</sup> K<sup>-1</sup>                 2.07   
Ac      12 W m<sup>-1</sup> K<sup>-1</sup>                 2.47   
Th      54 W m<sup>-1</sup> K<sup>-1</sup>                 2.45   
U       27 W m<sup>-1</sup> K<sup>-1</sup>                 2.41   

           Velocity of sound           Vickers hardness     X  Youngs modulus  \
H      1270 m s<sup>-1</sup>  no data MN m<sup>-2</sup>  2.20     no data GPa   
Li     6000 m s<sup>-1</sup>  no data MN m<sup>-2</sup>  0.98         4.9 GPa   
Be    13000 m s<sup>-1</sup>     1670 MN m<sup>-2</sup>  1.57         287 GPa   
B     16200 m s<sup>-1</sup>    49000 MN m<sup>-2</sup>  2.04     no data GPa   
C     18350 m s<sup>-1</sup>  no data MN m<sup>-2</sup>  2.55     no data GPa   
..                       ...                        ...   ...             ...   
Pb     1260 m s<sup>-1</sup>  no data MN m<sup>-2</sup>  2.33

In [6]:
cprops_df['Boiling point'] = [(a.replace('K', '', 1)) for a in cprops_df['Boiling point']]
cprops_df['Bulk modulus'] = cprops_df["Bulk modulus"].str.replace("GPa", "")
cprops_df['Critical temperature'] = cprops_df["Critical temperature"].str.replace("K", "")
cprops_df['Density of solid'] = cprops_df['Density of solid'].str.replace("no data", "NaN")
cprops_df['Density of solid'] = cprops_df["Density of solid"].str.replace("kg m<sup>-3</sup>", "")
cprops_df['Liquid range'] = [(a.replace('K', '', 1)) for a in cprops_df['Liquid range']]
cprops_df['Poissons ratio'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df['Poissons ratio']]
cprops_df['Poissons ratio'] = cprops_df['Poissons ratio'].str.replace("no data", "").astype(float)
cprops_df['Thermal conductivity'] = [float(a.replace('W m<sup>-1</sup> K<sup>-1</sup>', "", 1)) for a in cprops_df['Thermal conductivity']]
cprops_df['Velocity of sound'] = cprops_df['Velocity of sound'].str.replace("no data","NaN")
cprops_df['Velocity of sound'] = [(a.replace('m s<sup>-1</sup>', '', 1)) for a in cprops_df['Velocity of sound']]
cprops_df['Vickers hardness'] = cprops_df['Vickers hardness'].str.replace("no data", "NaN")
cprops_df['Vickers hardness'] = [(a.replace('MN m<sup>-2</sup>', '', 1)) for a in cprops_df['Vickers hardness']]
cprops_df['Youngs modulus'] = cprops_df['Youngs modulus'].str.replace("no data", "NaN")
cprops_df['Youngs modulus'] = [(a.replace('GPa', '', 1)) for a in cprops_df['Youngs modulus']]
cprops_df['Bulk modulus'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df['Bulk modulus']]
cprops_df['Bulk modulus'] = [(a.replace('liquid', '', 1)) for a in cprops_df['Bulk modulus']]
cprops_df['Bulk modulus'] = cprops_df['Bulk modulus'].str.replace(r"\(.*\)","",  regex=True).astype(float)
cprops_df['Melting point'] = cprops_df['Melting point'].str.replace("K", "")
cprops_df['Melting point'] = cprops_df['Melting point'].str.replace("white P", "")
cprops_df['Melting point'] = cprops_df['Melting point'].str.replace(r"\(.*\)","",  regex=True).astype(float)
cprops_df['Metallic radius'] = cprops_df['Metallic radius'].astype(str)
cprops_df['Metallic radius'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df['Metallic radius']]
cprops_df['Metallic radius'] = cprops_df['Metallic radius'].astype(float)
cprops_df['Common oxidation states'] = [len(a) for a in cprops_df['Common oxidation states']]
cprops_df['First Ionization Energy'] = [a[0] for a in cprops_df['Ionization energies']]

cprops_df = cprops_df.drop("Ionization energies", axis=1)

cprops_df['Critical temperature'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df['Critical temperature']]


In [7]:
cprops_df = cprops_df.apply(pd.to_numeric, errors='coerce')

In [8]:
# Computing mean values using mean function 
mvals = dict(cprops_df.mean())
mvals

{'Atomic mass': 107.06698397475002,
 'Atomic no': 44.7,
 'Atomic radius': 1.479999999999999,
 'Atomic radius calculated': 1.6537837837837837,
 'Boiling point': 2696.401625,
 'Bulk modulus': 91.6441176470588,
 'Common oxidation states': 1.6625,
 'Critical temperature': 1285.5176470588235,
 'Density of solid': 8067.890410958904,
 'Liquid range': 1317.8828749999998,
 'Melting point': 1383.99375,
 'Poissons ratio': 0.2942692307692307,
 'Thermal conductivity': 66.761243875,
 'Van der waals radius': 2.1264999999999996,
 'Velocity of sound': 3723.0015151515154,
 'Vickers hardness': 2108.3076923076924,
 'X': 1.7591249999999998,
 'Youngs modulus': 111.78688524590164,
 'Metallic radius': 1.622590909090909,
 'Electron affinity': 0.7264296744124998,
 'First Ionization Energy': 7.683228095414148}

In [9]:
# Iterating through variable with averages to replace the NaN values in element_data
for key, value in mvals.items():
    cprops_df.loc[cprops_df[key].isnull(),key] = value

In [10]:
filt_data_comp = filt_data
filt_data_comp['Composition'] = [Composition(c) for c in filt_data_comp["pretty_formula"]]
filt_data_comp['num_atoms'] = [c.num_atoms for c in filt_data_comp['Composition']]
filt_data_comp['volume_per_atom'] = filt_data_comp['volume']/filt_data_comp['num_atoms']

In [11]:
cprops_df_dict = cprops_df.to_dict()

rad_dict = cprops_df_dict['Atomic radius']

def radius_mean(composition):
    sumofradii = 0
    totnumatoms = 0
    for element, number in composition.items():
        sumofradii += (number*rad_dict[str(element)])
        totnumatoms += number
    return sumofradii/totnumatoms

atomic_radius = filt_data_comp['Composition'].apply(radius_mean)
atomic_radius

0       1.314286
1       1.275000
2       1.262500
3       1.125000
4       0.761765
          ...   
5614    0.957143
5615    1.000000
5616    0.883333
5617    0.766667
5618    0.835000
Name: Composition, Length: 5614, dtype: float64

In [12]:
#jojo version

def propertymean(property, composition):
    sumofproperty = 0
    totalnumatoms = 0
    for element, number in composition.items():
        sumofproperty += (number*cprops_df_dict[property][str(element)])
        totalnumatoms += number
    return sumofproperty/totalnumatoms

def maxofproperty(property, composition):
    propmax = None
    for element, number in composition.items():
        propertyvalue = cprops_df_dict[property][str(element)]
        if propmax:
            propmax = propertyvalue if propertyvalue > propmax else propmax
        else:
            propmax = propertyvalue
    return propmax

def minofproperty(property, composition):
    propmin = None
    for element, number in composition.items():
        propertyvalue = cprops_df_dict[property][str(element)]
        if propmin:
            propmin = propertyvalue if propertyvalue < propmin else propmin
        else:
            propmin = propertyvalue
    return propmin

In [13]:
avg_properties_df = pd.DataFrame()

for property in cprops_df.columns:
    individualpropertymean = partial(propertymean, property)
    averages = filt_data_comp['Composition'].apply(individualpropertymean)
    avg_properties_df[("average_" + property)] = averages
    
avg_properties_df.head()
print("Average properties Dimension: ", avg_properties_df.shape)

max_properties = pd.DataFrame()

for property in cprops_df.columns:
    individualpropertymax = partial(maxofproperty, property)
    max = filt_data_comp['Composition'].apply(individualpropertymax)
    max_properties[("max_" + property)] = max
    
min_properties = pd.DataFrame()

for property in cprops_df.columns:
    individualpropertymin = partial(minofproperty, property)
    min = filt_data_comp['Composition'].apply(individualpropertymin)
    min_properties[("min_" + property)] = min

Average properties Dimension:  (5614, 21)


In [14]:
design_matrix= pd.concat([filt_data_comp, avg_properties_df, min_properties, max_properties], axis=1)
design_matrix.columns

droplist2 = ['volume','energy', 'pretty_formula', 'Composition', 'average_Common oxidation states', 'min_Common oxidation states','max_Common oxidation states']
design_matrix = design_matrix.drop(columns=droplist2)
design_matrix

material_id  energy_per_atom  formation_energy_per_atom  nsites  \
0     mp-1001034        -3.715648                  -0.703661      14   
1     mp-1001780        -5.591101                  -1.699567       4   
2     mp-1001786        -5.900228                  -2.103385       4   
3     mp-1002124        -9.890380                  -0.298402       2   
4     mp-1004528        -5.614998                  -3.162482      17   
...          ...              ...                        ...     ...   
5614    mvc-6916        -7.098949                  -2.307339      14   
5615    mvc-6928        -6.543137                  -2.192463      14   
5616    mvc-6946        -6.122609                  -1.961400       6   
5617    mvc-7040        -8.067357                  -1.999722      18   
5618    mvc-7383        -6.225146                  -1.597210      20   

      nelements   density  band_gap  num_atoms  volume_per_atom  \
0             3  5.030727    0.7432        7.0        53.735123   
1             3  6.400668    1.5031        4.0        19.628830   
2             3  2.687084    1.5296        4.0        17.925309   
3             2  9.868236    0.5774        2.0        16.027883   
4             4  3.068458    6.3125       17.0        19.116437   
...         ...       ...       ...        ...              ...   
5614          3  4.200544    0.0516        7.0        22.383730   
5615          3  4.119621    1.7463        7.0        24.848833   
5616          2  5.131960    2.1009        3.0        32.509720   
5617          2  3.840256    3.4689        9.0        46.546747   
5618          3  2.941999    2.4238       10.0        31.765523   

      average_Atomic mass  ...  max_Poissons ratio  max_Thermal conductivity  \
0               81.397286  ...            0.330000                     160.0   
1               75.660750  ...            0.340000                     400.0   
2               29.006728  ...            0.294269                      85.0   
3               95.250350  ...            0.370000                     140.0   
4               35.324664  ...            0.440000                      36.0   
...                   ...  ...                 ...                       ...   
5614            28.311241  ...            0.294269                     160.0   
5615            30.823657  ...            0.310000                     200.0   
5616            50.236267  ...            0.360000                      67.0   
5617            53.823311  ...            0.300000                      48.0   
5618            28.139700  ...            0.294269                     120.0   

      max_Van der waals radius  max_Velocity of sound  max_Vickers hardness  \
0                         1.93            4602.000000           2108.307692   
1                         2.24            3723.001515           2108.307692   
2                         2.15            6000.000000           2108.307692   
3                         2.23           18350.000000           2108.307692   
4                         3.43           16200.000000          49000.000000   
...                        ...                    ...                   ...   
5614                      2.05            5150.000000           2108.307692   
5615                      2.31            4910.000000           2108.307692   
5616                      2.17            2500.000000           2108.307692   
5617                      2.16            4700.000000           2450.000000   
5618                      2.06            5940.000000           2108.307692   

      max_X  max_Youngs modulus  max_Metallic radius  max_Electron affinity  \
0      2.55           45.000000             1.670000               2.020605   
1      2.58          130.000000             1.735000               2.077105   
2      2.58          111.786885             1.641000               2.077105   
3      2.55          111.786885             1.622591               1.262114   
4      3.98          111.78688

In [15]:
IDs = list(filt_data["material_id"])
IDs = pd.DataFrame(IDs)

train_filt = train[train.index.isin(IDs.index)] 
train_filt

material_id  dielectric_poly_total
0      mp-555903               8.337936
1      mp-752658              14.735277
2        mp-3439              17.195305
3       mp-16135              21.593507
4       mp-36447               9.507068
...          ...                    ...
5609   mp-754117              13.378949
5610  mp-1539137              16.908907
5611  mp-1079559              11.776195
5612   mp-555908               6.241000
5613    mp-11653               5.887169

[5614 rows x 2 columns]

In [16]:
train_filt.set_index('material_id')

dielectric_poly_total
material_id                       
mp-555903                 8.337936
mp-752658                14.735277
mp-3439                  17.195305
mp-16135                 21.593507
mp-36447                  9.507068
...                            ...
mp-754117                13.378949
mp-1539137               16.908907
mp-1079559               11.776195
mp-555908                 6.241000
mp-11653                  5.887169

[5614 rows x 1 columns]

In [17]:
design_matrix

material_id  energy_per_atom  formation_energy_per_atom  nsites  \
0     mp-1001034        -3.715648                  -0.703661      14   
1     mp-1001780        -5.591101                  -1.699567       4   
2     mp-1001786        -5.900228                  -2.103385       4   
3     mp-1002124        -9.890380                  -0.298402       2   
4     mp-1004528        -5.614998                  -3.162482      17   
...          ...              ...                        ...     ...   
5614    mvc-6916        -7.098949                  -2.307339      14   
5615    mvc-6928        -6.543137                  -2.192463      14   
5616    mvc-6946        -6.122609                  -1.961400       6   
5617    mvc-7040        -8.067357                  -1.999722      18   
5618    mvc-7383        -6.225146                  -1.597210      20   

      nelements   density  band_gap  num_atoms  volume_per_atom  \
0             3  5.030727    0.7432        7.0        53.735123   
1             3  6.400668    1.5031        4.0        19.628830   
2             3  2.687084    1.5296        4.0        17.925309   
3             2  9.868236    0.5774        2.0        16.027883   
4             4  3.068458    6.3125       17.0        19.116437   
...         ...       ...       ...        ...              ...   
5614          3  4.200544    0.0516        7.0        22.383730   
5615          3  4.119621    1.7463        7.0        24.848833   
5616          2  5.131960    2.1009        3.0        32.509720   
5617          2  3.840256    3.4689        9.0        46.546747   
5618          3  2.941999    2.4238       10.0        31.765523   

      average_Atomic mass  ...  max_Poissons ratio  max_Thermal conductivity  \
0               81.397286  ...            0.330000                     160.0   
1               75.660750  ...            0.340000                     400.0   
2               29.006728  ...            0.294269                      85.0   
3               95.250350  ...            0.370000                     140.0   
4               35.324664  ...            0.440000                      36.0   
...                   ...  ...                 ...                       ...   
5614            28.311241  ...            0.294269                     160.0   
5615            30.823657  ...            0.310000                     200.0   
5616            50.236267  ...            0.360000                      67.0   
5617            53.823311  ...            0.300000                      48.0   
5618            28.139700  ...            0.294269                     120.0   

      max_Van der waals radius  max_Velocity of sound  max_Vickers hardness  \
0                         1.93            4602.000000           2108.307692   
1                         2.24            3723.001515           2108.307692   
2                         2.15            6000.000000           2108.307692   
3                         2.23           18350.000000           2108.307692   
4                         3.43           16200.000000          49000.000000   
...                        ...                    ...                   ...   
5614                      2.05            5150.000000           2108.307692   
5615                      2.31            4910.000000           2108.307692   
5616                      2.17            2500.000000           2108.307692   
5617                      2.16            4700.000000           2450.000000   
5618                      2.06            5940.000000           2108.307692   

      max_X  max_Youngs modulus  max_Metallic radius  max_Electron affinity  \
0      2.55           45.000000             1.670000               2.020605   
1      2.58          130.000000             1.735000               2.077105   
2      2.58          111.786885             1.641000               2.077105   
3      2.55          111.786885             1.622591               1.262114   
4      3.98          111.78688

In [18]:
design_matrix.set_index('material_id',inplace=True)
design_matrix

energy_per_atom  formation_energy_per_atom  nsites  nelements  \
material_id                                                                  
mp-1001034         -3.715648                  -0.703661      14          3   
mp-1001780         -5.591101                  -1.699567       4          3   
mp-1001786         -5.900228                  -2.103385       4          3   
mp-1002124         -9.890380                  -0.298402       2          2   
mp-1004528         -5.614998                  -3.162482      17          4   
...                      ...                        ...     ...        ...   
mvc-6916           -7.098949                  -2.307339      14          3   
mvc-6928           -6.543137                  -2.192463      14          3   
mvc-6946           -6.122609                  -1.961400       6          2   
mvc-7040           -8.067357                  -1.999722      18          2   
mvc-7383           -6.225146                  -1.597210      20          3   

              density  band_gap  num_atoms  volume_per_atom  \
material_id                                                   
mp-1001034   5.030727    0.7432        7.0        53.735123   
mp-1001780   6.400668    1.5031        4.0        19.628830   
mp-1001786   2.687084    1.5296        4.0        17.925309   
mp-1002124   9.868236    0.5774        2.0        16.027883   
mp-1004528   3.068458    6.3125       17.0        19.116437   
...               ...       ...        ...              ...   
mvc-6916     4.200544    0.0516        7.0        22.383730   
mvc-6928     4.119621    1.7463        7.0        24.848833   
mvc-6946     5.131960    2.1009        3.0        32.509720   
mvc-7040     3.840256    3.4689        9.0        46.546747   
mvc-7383     2.941999    2.4238       10.0        31.765523   

             average_Atomic mass  average_Atomic no  ...  max_Poissons ratio  \
material_id                                          ...                       
mp-1001034             81.397286          35.142857  ...            0.330000   
mp-1001780             75.660750          33.000000  ...            0.340000   
mp-1001786             29.006728          14.000000  ...            0.294269   
mp-1002124             95.250350          39.000000  ...            0.370000   
mp-1004528             35.324664          15.294118  ...            0.440000   
...                          ...                ...  ...                 ...   
mvc-6916               28.311241          13.428571  ...            0.294269   
mvc-6928               30.823657          14.857143  ...            0.310000   
mvc-6946               50.236267          22.000000  ...            0.360000   
mvc-7040               53.823311          22.888889  ...            0.300000   
mvc-7383               28.139700          13.400000  ...            0.294269   

             max_Thermal conductivity  max_Van der waals radius  \
material_id                                                       
mp-1001034                      160.0                      1.93   
mp-1001780                      400.0                      2.24   
mp-1001786                       85.0                      2.15   
mp-1002124                      140.0                      2.23   
mp-1004528                       36.0                      3.43   
...                               ...                       ...   
mvc-6916                        160.0                      2.05   
mvc-6928                        200.0                      2.31   
mvc-6946                         67.0                      2.17   
mvc-7040                         48.0                      2.16   
mvc-7383                        120.0                      2.06   

             max_Velocity of sound  max_Vickers hardness  max_X  \
material_id                                                       
mp-1001034             4602.000000           2108.307692   2.55   
mp-1001780             3723.001515           2108.307692   2.58 

In [19]:
X_train, X_test, y_train, y_test = train_test_split(design_matrix, 
                                                    train_filt,
                                                    test_size=0.1, 
                                                    random_state=120)

In [44]:
# Computing mean and standard devaitaion for train X and normalizing
mean_train_X = X_train.apply(np.mean, axis=0)
std_train_X = X_train.apply(np.std, axis=0)
norm_train_X = (X_train - mean_train_X) / std_train_X

# Computing mean and standard devaitaion for test X and normalizing 
mean_test_X = X_test.apply(np.mean, axis=0)
std_test_X = X_test.apply(np.std, axis=0)
norm_test_X = (X_test - mean_test_X) / std_test_X

# Test Data Querying

In [20]:
# Using material IDs provided in training data to get corresponding information from MPD
data22 = mpr.query(criteria={"task_id": {"$in":test["material_id"].to_list()}}, properties=["material_id","energy",
        "energy_per_atom",
        "volume",
        "formation_energy_per_atom",
        "nsites",
        "pretty_formula",                                                                                  
        "nelements",
        "density",  "band_gap"])
df_X = pd.DataFrame(data22)
display(df_X)

  0%|          | 0/1400 [00:00<?, ?it/s]

material_id      energy  energy_per_atom      volume  \
0        mp-1000   -8.646946        -4.323473   89.091084   
1       mp-10044  -11.376365        -5.688183   27.982045   
2       mp-10086  -42.877615        -7.146269   99.212472   
3     mp-1008858  -16.665812        -5.555271   80.958490   
4     mp-1008867  -11.760729        -3.920243   38.301187   
...          ...         ...              ...         ...   
1395    mvc-5908  -73.434572        -7.343457  120.736933   
1396    mvc-5921  -64.816637        -6.481664  143.204106   
1397    mvc-7386 -129.945458        -6.497273  386.834593   
1398    mvc-7701 -147.825353        -5.685591  330.380852   
1399    mvc-7761 -165.292243        -6.357394  383.421127   

      formation_energy_per_atom  nsites pretty_formula  nelements   density  \
0                     -1.792337       2           BaTe          2  4.937886   
1                     -0.019233       2            BAs          2  5.087631   
2                     -3.359731       6            YSF          3  4.685387   
3                     -0.944922       3         NdBiPd          3  9.427722   
4                     -0.701211       3          NaCuO          3  4.445388   
...                         ...     ...            ...        ...       ...   
1395                  -2.771448      10       Ca2CrWO6          4  5.666228   
1396                  -2.354943      10       Mg2SnWO6          4  5.185052   
1397                  -1.936434      20        ZnMo2O7          3  3.170408   
1398                  -1.957811      26       Zn2Sn3O8          3  6.181576   
1399                  -2.515768      26       Ca2Sn3O8          3  4.887634   

      band_gap  
0       1.8555  
1       1.2522  
2       1.3137  
3       0.0900  
4       0.0017  
...        ...  
1395    1.6101  
1396    2.2892  
1397    3.7020  
1398    1.2507  
1399    2.0677  

[1400 rows x 10 columns]

In [21]:
filt_data_X = df_X

listA_X = [a for a in filt_data_X["pretty_formula"]]
listB_X = [Composition(a) for a in listA_X]
listC_X = [a.elements for a in listB_X]

editC_X = [item for sublist in listC_X for item in sublist]
unique_editC_X = set(editC_X)
unique_editC_X

UL_editC_X = [a for a in unique_editC_X]
cprops_X = [a.data for a in UL_editC_X]

peel=set(UL_editC_X)
sy_editC_X = [a.symbol for a in UL_editC_X]
sy_editC_X

pd.set_option('display.max_rows', None)

cprops_df_X = pd.DataFrame(cprops_X, index=sy_editC_X)

droplist2 = droplist + ['Max oxidation state', 'Min oxidation state']

droplist2

cprops_df_X = cprops_df_X.drop(columns=droplist2)
cprops_df_X

Atomic mass  Atomic no Atomic radius Atomic radius calculated  \
H      1.007940          1          0.25                     0.53   
Li     6.941000          3          1.45                     1.67   
Be     9.012182          4          1.05                     1.12   
B     10.811000          5          0.85                     0.87   
C     12.010700          6           0.7                     0.67   
N     14.006700          7          0.65                     0.56   
O     15.999400          8           0.6                     0.48   
F     18.998403          9           0.5                     0.42   
Na    22.989769         11           1.8                      1.9   
Mg    24.305000         12           1.5                     1.45   
Al    26.981539         13          1.25                     1.18   
Si    28.085500         14           1.1                     1.11   
P     30.973762         15           1.0                     0.98   
S     32.065000         16           1.0                     0.88   
Cl    35.453000         17           1.0                     0.79   
K     39.098300         19           2.2                     2.43   
Ca    40.078000         20           1.8                     1.94   
Sc    44.955912         21           1.6                     1.84   
Ti    47.867000         22           1.4                     1.76   
V     50.941500         23          1.35                     1.71   
Cr    51.996100         24           1.4                     1.66   
Mn    54.938045         25           1.4                     1.61   
Fe    55.845000         26           1.4                     1.56   
Co    58.933195         27          1.35                     1.52   
Ni    58.693400         28          1.35                     1.49   
Cu    63.546000         29          1.35                     1.45   
Zn    65.409000         30          1.35                     1.42   
Ga    69.723000         31           1.3                     1.36   
Ge    72.640000         32          1.25                     1.25   
As    74.921600         33          1.15                     1.14   
Se    78.960000         34          1.15                     1.03   
Br    79.904000         35          1.15                     0.94   
Rb    85.467800         37          2.35                     2.65   
Sr    87.620000         38           2.0                     2.19   
Y     88.905850         39           1.8                     2.12   
Zr    91.224000         40          1.55                     2.06   
Nb    92.906380         41          1.45                     1.98   
Mo    95.940000         42          1.45                      1.9   
Tc    98.000000         43          1.35                     1.83   
Ru   101.070000         44           1.3                     1.78   
Rh   102.905500         45          1.35                     1.73   
Pd   106.420000         46           1.4                     1.69   
Ag   107.868200         47           1.6                     1.65   
Cd   112.411000         48          1.55                     1.61   
In   114.818000         49          1.55                     1.56   
Sn   118.710000         50          1.45                     1.45   
Sb   121.760000         51          1.45                     1.33   
Te   127.600000         52           1.4                     1.23   
I    126.904470         53           1.4                     1.15   
Xe   131.293000         54       no data                     1.08   
Cs   132.905452         55           2.6                     2.98   
Ba   137.327000         56          2.15                     2.53   
La   138.905470         57          1.95                  no data   
Ce   140.116000         58          1.85                  no data   
Pr   140.907650         59          1.85                     2.47   
Nd   144.242000         60          1.85                     2.06   
Sm   150.360000         62          1.85                     2.38   
Eu

In [22]:
cprops_df_X['Boiling point'] = [(a.replace('K', '', 1)) for a in cprops_df_X['Boiling point']]
cprops_df_X['Bulk modulus'] = cprops_df_X["Bulk modulus"].str.replace("GPa", "")
cprops_df_X['Critical temperature'] = cprops_df_X["Critical temperature"].str.replace("K", "")
cprops_df_X['Density of solid'] = cprops_df_X['Density of solid'].str.replace("no data", "NaN")
cprops_df_X['Density of solid'] = cprops_df_X["Density of solid"].str.replace("kg m<sup>-3</sup>", "")
cprops_df_X['Liquid range'] = [(a.replace('K', '', 1)) for a in cprops_df_X['Liquid range']]
cprops_df_X['Poissons ratio'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Poissons ratio']]
#cprops_df_X['Poissons ratio'] = cprops_df_X['Poissons ratio'].str.replace("no data", "").astype(float)
cprops_df_X['Thermal conductivity'] = [float(a.replace('W m<sup>-1</sup> K<sup>-1</sup>', "", 1)) for a in cprops_df_X['Thermal conductivity']]
cprops_df_X['Velocity of sound'] = cprops_df_X['Velocity of sound'].str.replace("no data","NaN")
cprops_df_X['Velocity of sound'] = [(a.replace('m s<sup>-1</sup>', '', 1)) for a in cprops_df_X['Velocity of sound']]
cprops_df_X['Vickers hardness'] = cprops_df_X['Vickers hardness'].str.replace("no data", "NaN", 1)
cprops_df_X['Vickers hardness'] = [(a.replace('MN m<sup>-2</sup>', '', 1)) for a in cprops_df_X['Vickers hardness']]
cprops_df_X['Youngs modulus'] = cprops_df_X['Youngs modulus'].str.replace("no data", "NaN", 1)
cprops_df_X['Youngs modulus'] = [(a.replace('GPa', '', 1)) for a in cprops_df_X['Youngs modulus']]
cprops_df_X['Bulk modulus'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Bulk modulus']]
cprops_df_X['Bulk modulus'] = [(a.replace('liquid', '', 1)) for a in cprops_df_X['Bulk modulus']]
cprops_df_X['Bulk modulus'] = cprops_df_X['Bulk modulus'].str.replace(r"\(.*\)","",  regex=True).astype(float)
cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace("K", "")
cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace("white P", "")
cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace(r"\(.*\)","",  regex=True).astype(float)
cprops_df_X['Metallic radius'] = cprops_df_X['Metallic radius'].astype(str)
cprops_df_X['Metallic radius'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Metallic radius']]
#cprops_df_X['Metallic radius'] = cprops_df_X['Metallic radius'].astype(float)
#cprops_df_X['Common oxidation states'] = [len(a) for a in cprops_df_X['Common oxidation states']]
cprops_df_X['First Ionization Energy'] = [a[0] for a in cprops_df_X['Ionization energies']]

cprops_df_X = cprops_df_X.drop("Ionization energies", axis=1)

cprops_df_X['Critical temperature'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Critical temperature']]


In [23]:
# cprops_df_X['Boiling point'] = [(a.replace('K', '', 1)) for a in cprops_df_X['Boiling point']]
# cprops_df_X['Bulk modulus'] = cprops_df_X["Bulk modulus"].str.replace("GPa", "", 1)
# cprops_df_X['Critical temperature'] = cprops_df_X["Critical temperature"].str.replace("K", "", 1)
# cprops_df_X['Density of solid'] = cprops_df_X['Density of solid'].str.replace("no data", "NaN", 1)
# cprops_df_X['Density of solid'] = cprops_df_X["Density of solid"].str.replace("kg m<sup>-3</sup>", "", 1)
# cprops_df_X['Liquid range'] = [(a.replace('K', '', 1)) for a in cprops_df_X['Liquid range']]
# cprops_df_X['Poissons ratio'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Poissons ratio']]
# cprops_df_X['Poissons ratio'] = cprops_df_X['Poissons ratio'].str.replace("no data", "").astype(float)
# cprops_df_X['Thermal conductivity'] = [float(a.replace('W m<sup>-1</sup> K<sup>-1</sup>', "", 1)) for a in cprops_df_X['Thermal conductivity']]
# cprops_df_X['Velocity of sound'] = cprops_df_X['Velocity of sound'].str.replace("no data","NaN", 1)
# cprops_df_X['Velocity of sound'] = [(a.replace('m s<sup>-1</sup>', '', 1)) for a in cprops_df_X['Velocity of sound']]
# cprops_df_X['Vickers hardness'] = cprops_df_X['Vickers hardness'].str.replace("no data", "NaN", 1)
# cprops_df_X['Vickers hardness'] = [(a.replace('MN m<sup>-2</sup>', '', 1)) for a in cprops_df_X['Vickers hardness']]
# cprops_df_X['Youngs modulus'] = cprops_df_X['Youngs modulus'].str.replace("no data", "NaN", 1)
# cprops_df_X['Youngs modulus'] = [(a.replace('GPa', '', 1)) for a in cprops_df_X['Youngs modulus']]
# cprops_df_X['Bulk modulus'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Bulk modulus']]
# cprops_df_X['Bulk modulus'] = [(a.replace('liquid', '', 1)) for a in cprops_df_X['Bulk modulus']]
# cprops_df_X['Bulk modulus'] = cprops_df_X['Bulk modulus'].str.replace(r"\(.*\)","",  regex=True).astype(float)
# cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace("K", "", 1)
# cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace("white P", "", 1)
# cprops_df_X['Melting point'] = cprops_df_X['Melting point'].str.replace(r"\(.*\)","",  regex=True).astype(float)
# cprops_df_X['Metallic radius'] = cprops_df_X['Metallic radius'].astype(str)
# cprops_df_X['Metallic radius'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Metallic radius']]
# cprops_df_X['Metallic radius'] = cprops_df_X['Metallic radius'].astype(float)
# #cprops_df_X['Common oxidation states'] = [len(a) for a in cprops_df_X['Common oxidation states']]
# cprops_df_X['First Ionization Energy'] = [a[0] for a in cprops_df_X['Ionization energies']]

# cprops_df_X = cprops_df_X.drop("Ionization energies", axis=1)

# cprops_df_X['Critical temperature'] = [(a.replace('no data', 'NaN', 1)) for a in cprops_df_X['Critical temperature']]


In [24]:
cprops_df_X

Atomic mass  Atomic no Atomic radius Atomic radius calculated  \
H      1.007940          1          0.25                     0.53   
Li     6.941000          3          1.45                     1.67   
Be     9.012182          4          1.05                     1.12   
B     10.811000          5          0.85                     0.87   
C     12.010700          6           0.7                     0.67   
N     14.006700          7          0.65                     0.56   
O     15.999400          8           0.6                     0.48   
F     18.998403          9           0.5                     0.42   
Na    22.989769         11           1.8                      1.9   
Mg    24.305000         12           1.5                     1.45   
Al    26.981539         13          1.25                     1.18   
Si    28.085500         14           1.1                     1.11   
P     30.973762         15           1.0                     0.98   
S     32.065000         16           1.0                     0.88   
Cl    35.453000         17           1.0                     0.79   
K     39.098300         19           2.2                     2.43   
Ca    40.078000         20           1.8                     1.94   
Sc    44.955912         21           1.6                     1.84   
Ti    47.867000         22           1.4                     1.76   
V     50.941500         23          1.35                     1.71   
Cr    51.996100         24           1.4                     1.66   
Mn    54.938045         25           1.4                     1.61   
Fe    55.845000         26           1.4                     1.56   
Co    58.933195         27          1.35                     1.52   
Ni    58.693400         28          1.35                     1.49   
Cu    63.546000         29          1.35                     1.45   
Zn    65.409000         30          1.35                     1.42   
Ga    69.723000         31           1.3                     1.36   
Ge    72.640000         32          1.25                     1.25   
As    74.921600         33          1.15                     1.14   
Se    78.960000         34          1.15                     1.03   
Br    79.904000         35          1.15                     0.94   
Rb    85.467800         37          2.35                     2.65   
Sr    87.620000         38           2.0                     2.19   
Y     88.905850         39           1.8                     2.12   
Zr    91.224000         40          1.55                     2.06   
Nb    92.906380         41          1.45                     1.98   
Mo    95.940000         42          1.45                      1.9   
Tc    98.000000         43          1.35                     1.83   
Ru   101.070000         44           1.3                     1.78   
Rh   102.905500         45          1.35                     1.73   
Pd   106.420000         46           1.4                     1.69   
Ag   107.868200         47           1.6                     1.65   
Cd   112.411000         48          1.55                     1.61   
In   114.818000         49          1.55                     1.56   
Sn   118.710000         50          1.45                     1.45   
Sb   121.760000         51          1.45                     1.33   
Te   127.600000         52           1.4                     1.23   
I    126.904470         53           1.4                     1.15   
Xe   131.293000         54       no data                     1.08   
Cs   132.905452         55           2.6                     2.98   
Ba   137.327000         56          2.15                     2.53   
La   138.905470         57          1.95                  no data   
Ce   140.116000         58          1.85                  no data   
Pr   140.907650         59          1.85                     2.47   
Nd   144.242000         60          1.85                     2.06   
Sm   150.360000         62          1.85                     2.38   
Eu

In [25]:
cprops_df_X['Atomic radius'] = cprops_df_X["Atomic radius"].astype(str)


In [26]:
cprops_df_X['Atomic radius'] = cprops_df_X["Atomic radius"].str.replace("no data", "NaN", 1)

In [27]:
cprops_df_X

Atomic mass  Atomic no Atomic radius Atomic radius calculated  \
H      1.007940          1          0.25                     0.53   
Li     6.941000          3          1.45                     1.67   
Be     9.012182          4          1.05                     1.12   
B     10.811000          5          0.85                     0.87   
C     12.010700          6           0.7                     0.67   
N     14.006700          7          0.65                     0.56   
O     15.999400          8           0.6                     0.48   
F     18.998403          9           0.5                     0.42   
Na    22.989769         11           1.8                      1.9   
Mg    24.305000         12           1.5                     1.45   
Al    26.981539         13          1.25                     1.18   
Si    28.085500         14           1.1                     1.11   
P     30.973762         15           1.0                     0.98   
S     32.065000         16           1.0                     0.88   
Cl    35.453000         17           1.0                     0.79   
K     39.098300         19           2.2                     2.43   
Ca    40.078000         20           1.8                     1.94   
Sc    44.955912         21           1.6                     1.84   
Ti    47.867000         22           1.4                     1.76   
V     50.941500         23          1.35                     1.71   
Cr    51.996100         24           1.4                     1.66   
Mn    54.938045         25           1.4                     1.61   
Fe    55.845000         26           1.4                     1.56   
Co    58.933195         27          1.35                     1.52   
Ni    58.693400         28          1.35                     1.49   
Cu    63.546000         29          1.35                     1.45   
Zn    65.409000         30          1.35                     1.42   
Ga    69.723000         31           1.3                     1.36   
Ge    72.640000         32          1.25                     1.25   
As    74.921600         33          1.15                     1.14   
Se    78.960000         34          1.15                     1.03   
Br    79.904000         35          1.15                     0.94   
Rb    85.467800         37          2.35                     2.65   
Sr    87.620000         38           2.0                     2.19   
Y     88.905850         39           1.8                     2.12   
Zr    91.224000         40          1.55                     2.06   
Nb    92.906380         41          1.45                     1.98   
Mo    95.940000         42          1.45                      1.9   
Tc    98.000000         43          1.35                     1.83   
Ru   101.070000         44           1.3                     1.78   
Rh   102.905500         45          1.35                     1.73   
Pd   106.420000         46           1.4                     1.69   
Ag   107.868200         47           1.6                     1.65   
Cd   112.411000         48          1.55                     1.61   
In   114.818000         49          1.55                     1.56   
Sn   118.710000         50          1.45                     1.45   
Sb   121.760000         51          1.45                     1.33   
Te   127.600000         52           1.4                     1.23   
I    126.904470         53           1.4                     1.15   
Xe   131.293000         54           NaN                     1.08   
Cs   132.905452         55           2.6                     2.98   
Ba   137.327000         56          2.15                     2.53   
La   138.905470         57          1.95                  no data   
Ce   140.116000         58          1.85                  no data   
Pr   140.907650         59          1.85                     2.47   
Nd   144.242000         60          1.85                     2.06   
Sm   150.360000         62          1.85                     2.38   
Eu

In [28]:
cprops_df_X.dtypes

Atomic mass                 float64
Atomic no                     int64
Atomic radius                object
Atomic radius calculated     object
Boiling point                object
Bulk modulus                float64
Common oxidation states      object
Critical temperature         object
Density of solid             object
Liquid range                 object
Melting point               float64
Poissons ratio               object
Thermal conductivity        float64
Van der waals radius        float64
Velocity of sound            object
Vickers hardness             object
X                           float64
Youngs modulus               object
Metallic radius              object
Electron affinity           float64
First Ionization Energy     float64
dtype: object

In [29]:
cprops_df_X = cprops_df_X.apply(pd.to_numeric, errors='coerce')
cprops_df_X.dtypes

Atomic mass                 float64
Atomic no                     int64
Atomic radius               float64
Atomic radius calculated    float64
Boiling point               float64
Bulk modulus                float64
Common oxidation states     float64
Critical temperature        float64
Density of solid            float64
Liquid range                float64
Melting point               float64
Poissons ratio              float64
Thermal conductivity        float64
Van der waals radius        float64
Velocity of sound           float64
Vickers hardness            float64
X                           float64
Youngs modulus              float64
Metallic radius             float64
Electron affinity           float64
First Ionization Energy     float64
dtype: object

In [30]:
# Computing mean values using mean function 
mvals_X = dict(cprops_df_X.mean()) #calculates 11
len(mvals_X)

for key, value in mvals_X.items():
    cprops_df_X.loc[cprops_df_X[key].isnull(),key] = value

display(cprops_df_X)

Atomic mass  Atomic no  Atomic radius  Atomic radius calculated  \
H      1.007940        1.0       0.250000                  0.530000   
Li     6.941000        3.0       1.450000                  1.670000   
Be     9.012182        4.0       1.050000                  1.120000   
B     10.811000        5.0       0.850000                  0.870000   
C     12.010700        6.0       0.700000                  0.670000   
N     14.006700        7.0       0.650000                  0.560000   
O     15.999400        8.0       0.600000                  0.480000   
F     18.998403        9.0       0.500000                  0.420000   
Na    22.989769       11.0       1.800000                  1.900000   
Mg    24.305000       12.0       1.500000                  1.450000   
Al    26.981539       13.0       1.250000                  1.180000   
Si    28.085500       14.0       1.100000                  1.110000   
P     30.973762       15.0       1.000000                  0.980000   
S     32.065000       16.0       1.000000                  0.880000   
Cl    35.453000       17.0       1.000000                  0.790000   
K     39.098300       19.0       2.200000                  2.430000   
Ca    40.078000       20.0       1.800000                  1.940000   
Sc    44.955912       21.0       1.600000                  1.840000   
Ti    47.867000       22.0       1.400000                  1.760000   
V     50.941500       23.0       1.350000                  1.710000   
Cr    51.996100       24.0       1.400000                  1.660000   
Mn    54.938045       25.0       1.400000                  1.610000   
Fe    55.845000       26.0       1.400000                  1.560000   
Co    58.933195       27.0       1.350000                  1.520000   
Ni    58.693400       28.0       1.350000                  1.490000   
Cu    63.546000       29.0       1.350000                  1.450000   
Zn    65.409000       30.0       1.350000                  1.420000   
Ga    69.723000       31.0       1.300000                  1.360000   
Ge    72.640000       32.0       1.250000                  1.250000   
As    74.921600       33.0       1.150000                  1.140000   
Se    78.960000       34.0       1.150000                  1.030000   
Br    79.904000       35.0       1.150000                  0.940000   
Rb    85.467800       37.0       2.350000                  2.650000   
Sr    87.620000       38.0       2.000000                  2.190000   
Y     88.905850       39.0       1.800000                  2.120000   
Zr    91.224000       40.0       1.550000                  2.060000   
Nb    92.906380       41.0       1.450000                  1.980000   
Mo    95.940000       42.0       1.450000                  1.900000   
Tc    98.000000       43.0       1.350000                  1.830000   
Ru   101.070000       44.0       1.300000                  1.780000   
Rh   102.905500       45.0       1.350000                  1.730000   
Pd   106.420000       46.0       1.400000                  1.690000   
Ag   107.868200       47.0       1.600000                  1.650000   
Cd   112.411000       48.0       1.550000                  1.610000   
In   114.818000       49.0       1.550000                  1.560000   
Sn   118.710000       50.0       1.450000                  1.450000   
Sb   121.760000       51.0       1.450000                  1.330000   
Te   127.600000       52.0       1.400000                  1.230000   
I    126.904470       53.0       1.400000                  1.150000   
Xe   131.293000       54.0       1.472436                  1.080000   
Cs   132.905452       55.0       2.600000                  2.980000   
Ba   137.327000       56.0       2.150000                  2.530000   
La   138.905470       57.0       1.950000                  1.636892   
Ce   140.116000       58.0       1.850000                  1.636892   
Pr   140.907650       59.0       1.850000                  2.470000   
Nd   144.242000       60.0  

In [31]:
cprops_df_X.dtypes

Atomic mass                 float64
Atomic no                   float64
Atomic radius               float64
Atomic radius calculated    float64
Boiling point               float64
Bulk modulus                float64
Common oxidation states     float64
Critical temperature        float64
Density of solid            float64
Liquid range                float64
Melting point               float64
Poissons ratio              float64
Thermal conductivity        float64
Van der waals radius        float64
Velocity of sound           float64
Vickers hardness            float64
X                           float64
Youngs modulus              float64
Metallic radius             float64
Electron affinity           float64
First Ionization Energy     float64
dtype: object

In [32]:
filt_data_comp_X = filt_data_X
filt_data_comp_X['Composition'] = [Composition(c) for c in filt_data_comp_X["pretty_formula"]]
filt_data_comp_X['num_atoms'] = [c.num_atoms for c in filt_data_comp_X['Composition']]
filt_data_comp_X['volume_per_atom'] = filt_data_comp_X['volume']/filt_data_comp_X['num_atoms']
filt_data_comp_X

material_id      energy  energy_per_atom       volume  \
0        mp-1000   -8.646946        -4.323473    89.091084   
1       mp-10044  -11.376365        -5.688183    27.982045   
2       mp-10086  -42.877615        -7.146269    99.212472   
3     mp-1008858  -16.665812        -5.555271    80.958490   
4     mp-1008867  -11.760729        -3.920243    38.301187   
5     mp-1009087  -38.652556        -4.831569   155.051465   
6       mp-10096  -84.572613        -3.844210   570.491249   
7     mp-1009894  -18.157914        -9.078957    33.282905   
8     mp-1013911 -313.454217        -6.530296   637.920695   
9     mp-1014013  -21.472932        -5.368233   534.970620   
10    mp-1014244  -29.937067        -7.484267    50.677512   
11      mp-10166  -32.240630        -4.030079   189.510574   
12    mp-1017567  -49.480157        -9.896031    71.711356   
13    mp-1018031  -20.056570        -5.014142    60.556641   
14    mp-1018040  -15.016540        -3.754135   107.896463   
15    mp-1018093  -14.751409        -3.687852    71.675405   
16      mp-10182  -10.239352        -3.413117    47.764547   
17    mp-1018630  -21.856850        -4.371370    89.402584   
18    mp-1018678  -31.752839        -5.292140   104.660709   
19    mp-1018737  -20.128448        -3.354741   153.047409   
20    mp-1019380  -60.232433        -7.529054    75.091895   
21    mp-1019558  -99.146152        -7.081868   190.037464   
22    mp-1019576 -225.448635        -6.262462   545.065099   
23    mp-1019589 -220.178056        -9.174086   301.042238   
24    mp-1019893 -330.919136        -8.272978   512.712050   
25    mp-1020019  -77.540291        -6.461691   118.725254   
26    mp-1020031 -118.092082        -5.904604   232.857861   
27    mp-1020122 -122.366222        -6.118311   279.474893   
28    mp-1020615 -347.906349        -7.906962   656.740262   
29    mp-1020797 -200.264507        -7.702481   411.576720   
30    mp-1021494  -32.660346        -2.969122   302.372098   
31      mp-10219  -49.672412        -8.278735    82.931171   
32    mp-1023132  -53.285042        -3.806074   299.999843   
33    mp-1023926  -19.476796        -6.492265   191.641337   
34    mp-1025267  -23.896614        -3.413802   300.502064   
35    mp-1025567  -51.545944        -6.443243   183.394154   
36    mp-1028668  -85.858604        -7.154884   357.049186   
37    mp-1029258  -23.090968        -4.618194    63.391152   
38    mp-1029262  -78.009288        -6.500774   142.415045   
39    mp-1029275  -64.191127        -8.023891   139.336333   
40    mp-1029294  -70.081442        -5.840120   174.330714   
41    mp-1029334  -61.507740        -5.125645   160.914404   
42    mp-1029385  -25.749869        -5.149974    51.806881   
43    mp-1029408  -88.079347        -7.339946   162.471388   
44    mp-1029542 -109.209468        -4.964067   329.054937   
45    mp-1029562 -216.821421        -4.517113   533.043514   
46    mp-1029592 -270.435330        -5.634069   582.758350   
47    mp-1029627 -172.059688        -7.169154   311.449854   
48    mp-1029652 -339.767868        -8.494197   486.249260   
49    mp-1029655  -97.258826        -6.947059   297.105486   
50    mp-1029834 -135.788602        -8.486788   211.220024   
51    mp-1029863 -547.167662        -6.672776  1628.009732   
52    mp-1029965 -504.701464        -6.154896  1596.013441   
53    mp-1029967 -563.858182        -6.876319  1845.695092   
54      mp-10341  -55.483075        -6.164786   126.148291   
55      mp-10426  -60.352964        -8.621852    83.304588   
56      mp-10461 -132.392279        -6.017831   331.052135   
57      mp-10517 -165.627421        -7.528519   287.711313   
58    mp-1057286   -4.554304        -2.277152    66.939421   
59      mp-10615  -11.871711        -3.957237    77.059923   
60    mp-1065514  -19.382498        -4.845625   141.750636   
61    mp-1069695  -15.543129        -3.108626   164.829684   
62    mp-1071955  -29.238479        -4.873080   180.845213   
63    mp-1078085  -24.168196        -

In [33]:




cprops_df_dict_X = cprops_df_X.to_dict()

rad_dict_X = cprops_df_dict_X['Atomic radius']

# atomic_radius_X = filt_data_comp_X['Composition'].apply(radius_mean)
# atomic_radius_X

In [34]:
cprops_df_dict_X

{'Atomic mass': {'H': 1.00794,
  'Li': 6.941,
  'Be': 9.012182,
  'B': 10.811,
  'C': 12.0107,
  'N': 14.0067,
  'O': 15.9994,
  'F': 18.9984032,
  'Na': 22.98976928,
  'Mg': 24.305,
  'Al': 26.9815386,
  'Si': 28.0855,
  'P': 30.973762,
  'S': 32.065,
  'Cl': 35.453,
  'K': 39.0983,
  'Ca': 40.078,
  'Sc': 44.955912,
  'Ti': 47.867,
  'V': 50.9415,
  'Cr': 51.9961,
  'Mn': 54.938045,
  'Fe': 55.845,
  'Co': 58.933195,
  'Ni': 58.6934,
  'Cu': 63.546,
  'Zn': 65.409,
  'Ga': 69.723,
  'Ge': 72.64,
  'As': 74.9216,
  'Se': 78.96,
  'Br': 79.904,
  'Rb': 85.4678,
  'Sr': 87.62,
  'Y': 88.90585,
  'Zr': 91.224,
  'Nb': 92.90638,
  'Mo': 95.94,
  'Tc': 98.0,
  'Ru': 101.07,
  'Rh': 102.9055,
  'Pd': 106.42,
  'Ag': 107.8682,
  'Cd': 112.411,
  'In': 114.818,
  'Sn': 118.71,
  'Sb': 121.76,
  'Te': 127.6,
  'I': 126.90447,
  'Xe': 131.293,
  'Cs': 132.9054519,
  'Ba': 137.327,
  'La': 138.90547,
  'Ce': 140.116,
  'Pr': 140.90765,
  'Nd': 144.242,
  'Sm': 150.36,
  'Eu': 151.964,
  'Tb': 15

In [35]:
# cprops_df_dict_X['Xe'] = None #adding new key-value pair

In [36]:
cprops_df_dict_X = cprops_df_X.to_dict()

rad_dict_X = cprops_df_dict_X['Atomic radius']

def radius_mean_X(composition):
    sumofradii = 0
    totnumatoms = 0
    for element, number in composition.items():
        sumofradii += (number*rad_dict_X[str(element)])
        totnumatoms += number
    return sumofradii/totnumatoms

atomic_radius_X = filt_data_comp_X['Composition'].apply(radius_mean_X)
atomic_radius_X

0       1.775000
1       1.000000
2       1.100000
3       1.616667
4       1.250000
5       1.112500
6       1.518182
7       1.125000
8       0.929167
9       1.000000
10      1.050000
11      1.337500
12      1.080000
13      1.237500
14      1.325000
15      1.150000
16      1.266667
17      1.240000
18      0.941667
19      1.566667
20      0.900000
21      1.046429
22      1.211111
23      0.954167
24      0.980000
25      0.958333
26      1.160000
27      0.770000
28      0.804545
29      0.784615
30      1.250000
31      0.966667
32      1.250000
33      1.383333
34      1.657143
35      1.012500
36      1.216667
37      1.160000
38      1.000000
39      1.212500
40      1.050000
41      1.016667
42      1.130000
43      1.066667
44      1.350000
45      1.200000
46      1.241667
47      1.050000
48      0.957500
49      1.328571
50      1.087500
51      1.336585
52      1.328049
53      1.391463
54      0.916667
55      0.842857
56      1.168182
57      0.840909
58      1.4250

In [37]:
#jojo version

def propertymean_X(property, composition):
    sumofproperty = 0
    totalnumatoms = 0
    for element, number in composition.items():
        sumofproperty += (number*cprops_df_dict_X[property][str(element)])
        totalnumatoms += number
    return sumofproperty/totalnumatoms

def maxofproperty_X(property, composition):
    propmax = None
    for element, number in composition.items():
        propertyvalue = cprops_df_dict_X[property][str(element)]
        if propmax:
            propmax = propertyvalue if propertyvalue > propmax else propmax
        else:
            propmax = propertyvalue
    return propmax

def minofproperty_X(property, composition):
    propmin = None
    for element, number in composition.items():
        propertyvalue = cprops_df_dict_X[property][str(element)]
        if propmin:
            propmin = propertyvalue if propertyvalue < propmin else propmin
        else:
            propmin = propertyvalue
    return propmin

In [38]:
avg_properties_df_X = pd.DataFrame()

for property in cprops_df_X.columns:
    individualpropertymean = partial(propertymean_X, property)
    averages = filt_data_comp_X['Composition'].apply(individualpropertymean)
    avg_properties_df_X[("average_" + property)] = averages
    
avg_properties_df_X.head()
print("Average properties Dimension: ", avg_properties_df_X.shape)

max_properties_X = pd.DataFrame()

for property in cprops_df.columns:
    individualpropertymax = partial(maxofproperty_X, property)
    max = filt_data_comp_X['Composition'].apply(individualpropertymax)
    max_properties_X[("max_" + property)] = max
    
min_properties_X = pd.DataFrame()

for property in cprops_df.columns:
    individualpropertymin = partial(minofproperty_X, property)
    min = filt_data_comp_X['Composition'].apply(individualpropertymin)
    min_properties_X[("min_" + property)] = min

Average properties Dimension:  (1400, 21)


In [39]:
filt_data_comp_X

material_id      energy  energy_per_atom       volume  \
0        mp-1000   -8.646946        -4.323473    89.091084   
1       mp-10044  -11.376365        -5.688183    27.982045   
2       mp-10086  -42.877615        -7.146269    99.212472   
3     mp-1008858  -16.665812        -5.555271    80.958490   
4     mp-1008867  -11.760729        -3.920243    38.301187   
5     mp-1009087  -38.652556        -4.831569   155.051465   
6       mp-10096  -84.572613        -3.844210   570.491249   
7     mp-1009894  -18.157914        -9.078957    33.282905   
8     mp-1013911 -313.454217        -6.530296   637.920695   
9     mp-1014013  -21.472932        -5.368233   534.970620   
10    mp-1014244  -29.937067        -7.484267    50.677512   
11      mp-10166  -32.240630        -4.030079   189.510574   
12    mp-1017567  -49.480157        -9.896031    71.711356   
13    mp-1018031  -20.056570        -5.014142    60.556641   
14    mp-1018040  -15.016540        -3.754135   107.896463   
15    mp-1018093  -14.751409        -3.687852    71.675405   
16      mp-10182  -10.239352        -3.413117    47.764547   
17    mp-1018630  -21.856850        -4.371370    89.402584   
18    mp-1018678  -31.752839        -5.292140   104.660709   
19    mp-1018737  -20.128448        -3.354741   153.047409   
20    mp-1019380  -60.232433        -7.529054    75.091895   
21    mp-1019558  -99.146152        -7.081868   190.037464   
22    mp-1019576 -225.448635        -6.262462   545.065099   
23    mp-1019589 -220.178056        -9.174086   301.042238   
24    mp-1019893 -330.919136        -8.272978   512.712050   
25    mp-1020019  -77.540291        -6.461691   118.725254   
26    mp-1020031 -118.092082        -5.904604   232.857861   
27    mp-1020122 -122.366222        -6.118311   279.474893   
28    mp-1020615 -347.906349        -7.906962   656.740262   
29    mp-1020797 -200.264507        -7.702481   411.576720   
30    mp-1021494  -32.660346        -2.969122   302.372098   
31      mp-10219  -49.672412        -8.278735    82.931171   
32    mp-1023132  -53.285042        -3.806074   299.999843   
33    mp-1023926  -19.476796        -6.492265   191.641337   
34    mp-1025267  -23.896614        -3.413802   300.502064   
35    mp-1025567  -51.545944        -6.443243   183.394154   
36    mp-1028668  -85.858604        -7.154884   357.049186   
37    mp-1029258  -23.090968        -4.618194    63.391152   
38    mp-1029262  -78.009288        -6.500774   142.415045   
39    mp-1029275  -64.191127        -8.023891   139.336333   
40    mp-1029294  -70.081442        -5.840120   174.330714   
41    mp-1029334  -61.507740        -5.125645   160.914404   
42    mp-1029385  -25.749869        -5.149974    51.806881   
43    mp-1029408  -88.079347        -7.339946   162.471388   
44    mp-1029542 -109.209468        -4.964067   329.054937   
45    mp-1029562 -216.821421        -4.517113   533.043514   
46    mp-1029592 -270.435330        -5.634069   582.758350   
47    mp-1029627 -172.059688        -7.169154   311.449854   
48    mp-1029652 -339.767868        -8.494197   486.249260   
49    mp-1029655  -97.258826        -6.947059   297.105486   
50    mp-1029834 -135.788602        -8.486788   211.220024   
51    mp-1029863 -547.167662        -6.672776  1628.009732   
52    mp-1029965 -504.701464        -6.154896  1596.013441   
53    mp-1029967 -563.858182        -6.876319  1845.695092   
54      mp-10341  -55.483075        -6.164786   126.148291   
55      mp-10426  -60.352964        -8.621852    83.304588   
56      mp-10461 -132.392279        -6.017831   331.052135   
57      mp-10517 -165.627421        -7.528519   287.711313   
58    mp-1057286   -4.554304        -2.277152    66.939421   
59      mp-10615  -11.871711        -3.957237    77.059923   
60    mp-1065514  -19.382498        -4.845625   141.750636   
61    mp-1069695  -15.543129        -3.108626   164.829684   
62    mp-1071955  -29.238479        -4.873080   180.845213   
63    mp-1078085  -24.168196        -

In [40]:
design_matrix_X= pd.concat([filt_data_comp_X, avg_properties_df_X, min_properties_X, max_properties_X], axis=1)
design_matrix_X.columns

droplist2 = ['volume','energy', 'pretty_formula', 'Composition', 'average_Common oxidation states', 'min_Common oxidation states','max_Common oxidation states']

design_matrix_X = design_matrix_X.drop(columns=droplist2)
design_matrix_X

material_id  energy_per_atom  formation_energy_per_atom  nsites  \
0        mp-1000        -4.323473              -1.792337e+00       2   
1       mp-10044        -5.688183              -1.923329e-02       2   
2       mp-10086        -7.146269              -3.359731e+00       6   
3     mp-1008858        -5.555271              -9.449219e-01       3   
4     mp-1008867        -3.920243              -7.012111e-01       3   
5     mp-1009087        -4.831569              -2.116146e-01       8   
6       mp-10096        -3.844210              -7.818146e-01      22   
7     mp-1009894        -9.078957              -1.917217e-01       2   
8     mp-1013911        -6.530296              -2.496547e+00      48   
9     mp-1014013        -5.368233               4.505289e-02       4   
10    mp-1014244        -7.484267              -1.056240e+00       4   
11      mp-10166        -4.030079              -1.017673e+00       8   
12    mp-1017567        -9.896031              -2.037571e+00       5   
13    mp-1018031        -5.014142              -1.925789e+00       4   
14    mp-1018040        -3.754135              -1.207731e+00       4   
15    mp-1018093        -3.687852              -4.666521e-01       4   
16      mp-10182        -3.413117              -5.525608e-01       3   
17    mp-1018630        -4.371370              -6.123091e-01       5   
18    mp-1018678        -5.292140              -1.901286e+00       6   
19    mp-1018737        -3.354741              -6.478810e-01       6   
20    mp-1019380        -7.529054              -1.313303e+00       8   
21    mp-1019558        -7.081868              -3.388516e+00      14   
22    mp-1019576        -6.262462              -1.236781e+00      36   
23    mp-1019589        -9.174086              -3.821235e+00      24   
24    mp-1019893        -8.272978              -1.531700e+00      40   
25    mp-1020019        -6.461691              -2.182535e+00      12   
26    mp-1020031        -5.904604              -1.192823e+00      20   
27    mp-1020122        -6.118311              -2.292058e+00      20   
28    mp-1020615        -7.906962              -3.193614e+00      44   
29    mp-1020797        -7.702481              -3.016564e+00      26   
30    mp-1021494        -2.969122              -1.066334e+00      11   
31      mp-10219        -8.278735              -4.234639e+00       6   
32    mp-1023132        -3.806074              -2.139102e+00      14   
33    mp-1023926        -6.492265              -7.735588e-02       3   
34    mp-1025267        -3.413802              -1.936949e+00       7   
35    mp-1025567        -6.443243              -2.229575e+00       8   
36    mp-1028668        -7.154884              -7.473504e-01      12   
37    mp-1029258        -4.618194              -5.335280e-01       5   
38    mp-1029262        -6.500774              -5.909917e-01      12   
39    mp-1029275        -8.023891              -1.488359e+00       8   
40    mp-1029294        -5.840120              -2.149653e-01      12   
41    mp-1029334        -5.125645              -4.142207e-02      12   
42    mp-1029385        -5.149974              -4.069568e-01       5   
43    mp-1029408        -7.339946              -1.147860e+00      12   
44    mp-1029542        -4.964067              -3.705338e-01      22   
45    mp-1029562        -4.517113              -4.532135e-01      48   
46    mp-1029592        -5.634069              -9.511048e-01      48   
47    mp-1029627        -7.169154              -5.865311e-01      24   
48    mp-1029652        -8.494197              -1.523409e+00      40   
49    mp-1029655        -6.947059              -9.636323e-01      14   
50    mp-1029834        -8.486788              -1.622031e+00      16   
51    mp-1029863        -6.672776              -4.565655e-01      82   
52    mp-1029965        -6.154896              -1.464984e-01      82   
53    mp-1029967        -6.876319              -6.199323e-01      82   
54      mp-10341        -6.164786            

In [41]:
design_matrix_X.set_index('material_id',inplace=True)
design_matrix_X

energy_per_atom  formation_energy_per_atom  nsites  nelements  \
material_id                                                                  
mp-1000            -4.323473              -1.792337e+00       2          2   
mp-10044           -5.688183              -1.923329e-02       2          2   
mp-10086           -7.146269              -3.359731e+00       6          3   
mp-1008858         -5.555271              -9.449219e-01       3          3   
mp-1008867         -3.920243              -7.012111e-01       3          3   
mp-1009087         -4.831569              -2.116146e-01       8          3   
mp-10096           -3.844210              -7.818146e-01      22          4   
mp-1009894         -9.078957              -1.917217e-01       2          2   
mp-1013911         -6.530296              -2.496547e+00      48          4   
mp-1014013         -5.368233               4.505289e-02       4          1   
mp-1014244         -7.484267              -1.056240e+00       4          3   
mp-10166           -4.030079              -1.017673e+00       8          3   
mp-1017567         -9.896031              -2.037571e+00       5          3   
mp-1018031         -5.014142              -1.925789e+00       4          3   
mp-1018040         -3.754135              -1.207731e+00       4          2   
mp-1018093         -3.687852              -4.666521e-01       4          4   
mp-10182           -3.413117              -5.525608e-01       3          3   
mp-1018630         -4.371370              -6.123091e-01       5          3   
mp-1018678         -5.292140              -1.901286e+00       6          4   
mp-1018737         -3.354741              -6.478810e-01       6          3   
mp-1019380         -7.529054              -1.313303e+00       8          3   
mp-1019558         -7.081868              -3.388516e+00      14          5   
mp-1019576         -6.262462              -1.236781e+00      36          3   
mp-1019589         -9.174086              -3.821235e+00      24          3   
mp-1019893         -8.272978              -1.531700e+00      40          3   
mp-1020019         -6.461691              -2.182535e+00      12          4   
mp-1020031         -5.904604              -1.192823e+00      20          4   
mp-1020122         -6.118311              -2.292058e+00      20          3   
mp-1020615         -7.906962              -3.193614e+00      44          4   
mp-1020797         -7.702481              -3.016564e+00      26          3   
mp-1021494         -2.969122              -1.066334e+00      11          3   
mp-10219           -8.278735              -4.234639e+00       6          3   
mp-1023132         -3.806074              -2.139102e+00      14          4   
mp-1023926         -6.492265              -7.735588e-02       3          2   
mp-1025267         -3.413802              -1.936949e+00       7          3   
mp-1025567         -6.443243              -2.229575e+00       8          3   
mp-1028668         -7.154884              -7.473504e-01      12          5   
mp-1029258         -4.618194              -5.335280e-01       5          3   
mp-1029262         -6.500774              -5.909917e-01      12          3   
mp-1029275         -8.023891              -1.488359e+00       8          3   
mp-1029294         -5.840120              -2.149653e-01      12          3   
mp-1029334         -5.125645              -4.142207e-02      12          3   
mp-1029385         -5.149974              -4.069568e-01       5          3   
mp-1029408         -7.339946              -1.147860e+00      12          3   
mp-1029542         -4.964067              -3.705338e-01      22          3   
mp-1029562         -4.517113              -4.532135e-01      48          3   
mp-1029592         -5.634069              -9.511048e-01      48          3   
mp-1029627         -7.169154              -5.865311e-01      24          3   
mp-1029652         -8.494197              -1.523409e+00      40          3   
mp-1029655         -6.947059       

In [42]:
lo = design_matrix_X.isnull().sum()
lo

energy_per_atom                     0
formation_energy_per_atom           0
nsites                              0
nelements                           0
density                             0
band_gap                            0
num_atoms                           0
volume_per_atom                     0
average_Atomic mass                 0
average_Atomic no                   0
average_Atomic radius               0
average_Atomic radius calculated    0
average_Boiling point               0
average_Bulk modulus                0
average_Critical temperature        0
average_Density of solid            0
average_Liquid range                0
average_Melting point               0
average_Poissons ratio              0
average_Thermal conductivity        0
average_Van der waals radius        0
average_Velocity of sound           0
average_Vickers hardness            0
average_X                           0
average_Youngs modulus              0
average_Metallic radius             0
average_Elec

In [46]:
from sklearn.linear_model import LinearRegression
linear_model = LinearRegression()
linear_model.fit(norm_train_X, y_train['dielectric_poly_total'])
#linear_predictions = pd.DataFrame(linear_model.predict(norm_test_X),
                                #  columns = ['dielectric_poly_total'])
linear_predictions = linear_model.predict(X_test)

# linear_model.score(design_matrix, train_filt['dielectric_poly_total']) #CLOSE WE GOT TO PREDICTING x TEST....PROBABLY USE SOME FIXING A BETTER WAY TO TELL US HOW CLOSE OUR PREDICTION IS TO ACTUAL X TEST

In [47]:
linear_model.score?

In [48]:
X_data_test = design_matrix_X

#F_linear_predictions = linear_model.predict(df2)
Final_linear_predictions_X = linear_model.predict(X_data_test)
flp_X = pd.DataFrame(Final_linear_predictions_X)

d_list=[test, flp_X]

newsubs = pd.concat(d_list, axis=1)
newsubs_update = newsubs.rename(columns={0:'dielectric_poly_total'})
newsubs_update.to_csv("submission_test_6_12-02-2021.csv", index=False)

In [49]:
y_train.head()

material_id  dielectric_poly_total
5       mp-29175              25.723003
886      mp-7436              12.047716
3192   mp-765958               7.014766
5364   mp-989548              12.402333
595      mp-6675               6.223076

#### SVR

In [50]:
from sklearn import svm, datasets
from sklearn.model_selection import cross_val_score
model_svr = svm.SVR(kernel='rbf', C=0.001
                    , epsilon=0.001,  tol=1e-5)
scores = -cross_val_score(model_svr, norm_train_X, y_train['dielectric_poly_total'], cv=5, scoring='neg_mean_absolute_error')

In [62]:
cross_val_score?

In [51]:
# Training score
np.mean(scores)

7.930859837414291

In [52]:
# Training score
np.mean(scores)

7.930859837414291

In [53]:
# Testing score
model_svr = svm.SVR(kernel='rbf', C=0.1, epsilon=0.1,  tol=1e-5)
model_svr.fit(norm_train_X, y_train['dielectric_poly_total'])
scores = -cross_val_score(model_svr, norm_test_X, y_test['dielectric_poly_total'], cv=5, scoring='neg_mean_absolute_error')
print(np.mean(np.abs(y_test['dielectric_poly_total'] - model_svr.predict(norm_test_X))))
np.mean(scores)

8.272759195284086


8.249384012637083

#### Random Forest Regressor

In [54]:
from sklearn.ensemble import RandomForestRegressor
model_rfr = RandomForestRegressor(n_estimators=100, max_depth=35, min_samples_split=2 , random_state=42)
scores = -cross_val_score(model_rfr, X_train, y_train['dielectric_poly_total'], cv=5, scoring='neg_mean_absolute_error')

In [55]:
# Training score
np.mean(scores)

9.76191447785529

In [56]:
# Training score
np.mean(scores)

9.76191447785529

In [57]:
# Testing score
model_rfr = RandomForestRegressor(n_estimators=100, max_depth=10, min_samples_split=4 , random_state=42)
model_rfr.fit(X_train, y_train['dielectric_poly_total'])
scores = -cross_val_score(model_rfr, X_test, y_test['dielectric_poly_total'], cv=5, scoring='neg_mean_absolute_error')
print(np.mean(np.abs(y_test['dielectric_poly_total'] - model_rfr.predict(X_test))))
np.mean(scores)

9.120111766335887


9.974078516982374

In [58]:
X_train.head()

energy_per_atom  formation_energy_per_atom  nsites  nelements  \
material_id                                                                  
mp-1006888         -5.846844                  -2.216231       4          3   
mp-1226281         -4.666992                  -0.238231      10          4   
mp-555229          -5.659234                  -1.007094      18          4   
mp-961675          -6.876485                  -1.034626       3          3   
mp-1190488         -6.908359                  -3.107679      24          3   

              density  band_gap  num_atoms  volume_per_atom  \
material_id                                                   
mp-1006888   3.028430    2.3526        4.0        26.337598   
mp-1226281   4.641012    0.7251       10.0        24.887337   
mp-555229    1.237595    5.0410        9.0        18.801127   
mp-961675    4.894903    0.7107        3.0        15.223106   
mp-1190488   3.653744    3.0642       12.0        25.172896   

             average_Atomic mass  average_Atomic no  ...  max_Poissons ratio  \
material_id                                          ...                       
mp-1006888             48.033538          22.500000  ...            0.294269   
mp-1226281             69.557182          30.500000  ...            0.370000   
mp-555229               7.006211           3.777778  ...            0.294269   
mp-961675              44.874358          21.333333  ...            0.310000   
mp-1190488             27.694413          13.000000  ...            0.350000   

             max_Thermal conductivity  max_Van der waals radius  \
material_id                                                       
mp-1006888                      100.0                      2.75   
mp-1226281                      430.0                      2.11   
mp-555229                       140.0                      1.70   
mp-961675                        91.0                      2.15   
mp-1190488                      235.0                      2.18   

             max_Velocity of sound  max_Vickers hardness  max_X  \
material_id                                                       
mp-1006888             3723.001515           2108.307692   2.58   
mp-1226281             5940.000000           2108.307692   2.55   
mp-555229             18350.000000           2108.307692   3.44   
mp-961675              4970.000000           2108.307692   2.19   
mp-1190488             5100.000000           2108.307692   3.44   

             max_Youngs modulus  max_Metallic radius  max_Electron affinity  \
material_id                                                                   
mp-1006888           111.786885             2.381000               2.077105   
mp-1226281           279.000000             1.622591               2.020605   
mp-555229            111.786885             1.622591               1.461105   
mp-961675            200.000000             1.641000               1.157161   
mp-1190488           111.786885             1.622591               1.461105   

             max_First Ionization Energy  
material_id                               
mp-1006888                     10.360010  
mp-1226281                     10.486686  
mp-555229                      14.534130  
mp-961675                      10.486686  
mp-1190488                     13.618055  

[5 rows x 68 columns]

In [60]:
# #‘neg_mean_absolute_error’

# # metrics.mean_absolute_error
# X, y = datasets.load_iris(return_X_y=True)
# clf = svm.SVC(random_state=0)
# cross_val_score(clf, X, y, cv=5, scoring='recall_macro')

# model = svm.SVC()
# cross_val_score(model, X, y, cv=5, scoring='wrong_choice')

In [61]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
import tensorflow.keras.layers as layers
import tensorflow as tf



# Creating model
model = Sequential()
model.add(layers.Dense(68, activation='relu', input_shape=(1,))) # Number of features, intput layer
model.add(layers.Dense(64, activation='relu')) # Beginning of hidden layers
model.add(layers.Dense(32, activation='relu'))
model.add(layers.Dense(16, activation='relu'))
model.add(layers.Dense(8, activation='relu')) 
model.add(layers.Dense(1)) # Output layer

# Compiling model
model.compile(loss='mean_absolute_error', optimizer='adam', metrics=['accuracy', 'mean_absolute_error']) # Remove mean_absolute_error if you're getting error

# Fitting and gathering results
model.fit(X_train, y_train, epochs=30, batch_size=500)
results = model.evaluate(X_test, y_test)


ValueError: Failed to convert a NumPy array to a Tensor (Unsupported object type float).